## PDF to CSV (New)

### Test

In [ ]:
### Test

import pdfplumber
import pandas as pd

# Path to your PDF file
pdf_path = "/Volumes/Ping Pong/TS2/00194909_f_20181023143245.pdf"


# Open the PDF file using pdfplumber
with pdfplumber.open(pdf_path) as pdf:
    start_page = None
    dfs = []

    # Iterate over each page in the PDF
    for i, page in enumerate(pdf.pages):
        page_text = page.extract_text()
        
        # Check if "1. Location Parameters" is present in the page text
        if "1. Location Parameters" in page_text:
            start_page = i
            break

    if start_page is not None:
        # Read the PDF file again, starting from the identified page
        for page in pdf.pages[start_page:]:
            tables = page.extract_tables()
            for table in tables:
                # Generate unique column names for each table
                columns = [f"Column_{i}" for i in range(len(table[0]))]
                df = pd.DataFrame(table[0:], columns=columns)
                dfs.append(df)

        if dfs:
            # Concatenate all tables into a single DataFrame
            combined_df = pd.concat(dfs, ignore_index=True)

            # Shift first three rows to column 2
            combined_df.loc[0:3, 'Column_1'] = combined_df['Column_0']
            
            # Drop unnecessary columns
            combined_df = combined_df.drop(columns=["Column_0","Column_3", "Column_7", "Column_8"])

            # Drop empty rows
            combined_df = combined_df.dropna(how='all')

            # Remove line breaks
            combined_df = combined_df.replace('\n', ' ', regex=True)

            # Save the combined DataFrame as a CSV file
            output_csv = "output.csv"
            combined_df.to_csv(output_csv, header=None,index=False)
            print(f"Tables saved in {output_csv}")
        else:
            print("No tables found in the PDF.")
    else:
        print("Unable to find '1. Location Parameters' in the PDF.")

# print(combined_df)


In [ ]:
### Loop Test

import pandas as pd
import os
import glob

## Change folder path and output_csv for each run
# Path to the folder containing the files
folder_path = "/Users/sid/Documents/MA/AN/"

# Get a list of files in the folder
file_list = glob.glob(os.path.join(folder_path, "*.csv"))

# Initialize an empty DataFrame to store the combined results
final_df = pd.DataFrame()

# Initialize a dictionary to store the shape counts
shape_counts = {}

# Loop over each file
for file_path in file_list:
    # Read the file into a DataFrame
    df2 = pd.read_csv(file_path)

    ## State info
    df4 = df2.drop(df2.index[3:], inplace=False) # only keep required rows
    df4 = df4.iloc[:, [0, 1]] # drops unnecesary columns
    df4 = df4.transpose().reset_index()
    df4.columns = df4.iloc[0]
    df4 = df4[1:]  # Remove the header row

    ## District info
    df5 = df2.drop(df2.index[2:], inplace=False)
    df5 = df5.iloc[:, [2, 4]]
    df5 = df5.transpose().reset_index()
    df5.columns = df5.iloc[0]
    df5 = df5[1:]  # Remove the header row

    ## Village Parameters
    df3 = df2.iloc[4:].transpose()
    # Extract the header row and set it as the column names
    df3.columns = df3.iloc[0]
    df3 = df3[1:]  # Remove the header row
    df3 = df3.iloc[1:]

    df3 = df3.reset_index(drop=True)

    # # Remove row 1,3
    rows_to_drop = [0,2] 
    df3 = df3.drop(rows_to_drop)
    df3 = df3.fillna(0)

    # Reset the index
    # df3 = df3.reset_index(drop=True)
    # df3 = df3.dropna(how='all')
    combined_df = pd.concat([df4, df5,df3], axis=1)
    # print(combined_df.shape[1])

    # Get the shape of combined_df
    df_shape = combined_df.shape

    # Increment the count for the shape in the dictionary
    if df_shape in shape_counts:
        shape_counts[df_shape] += 1
    else:
        shape_counts[df_shape] = 1

    if combined_df.shape[1] == 54:
        final_df = final_df.append(combined_df, ignore_index=True)
     
output_csv = "/Users/sid/Documents/MA_20/AN.csv"
final_df.to_csv(output_csv, index=False)
print(f"Combined results saved in {output_csv}")

# Print the shape counts
print("Shape Counts:")
for shape, count in shape_counts.items():
    print(f"Shape: {shape}, Count: {count}")
    

### PDF to CSV loop

#### 2020 Data

In [ ]:
import glob
import os
import pdfplumber
import pandas as pd

# Folder path containing the PDF files
folder_path = "/Users/sid/Documents/MA/TN/"

# Output folder path for saving CSV files
output_folder = "/Users/sid/Documents/MA_20/TN/"

# Get a list of PDF files in the folder
pdf_files = glob.glob(folder_path + "*.pdf")

# Function to shift data by 2 columns if Column 3 is not empty. Some pdfs formatting causes page 3 data to be misinterpretted. 
def shift_data(row):
    if row.name >= 30 and pd.notnull(row[3]):  # Check if row index is >= 30 and Column 3 is not empty
        row[5:] = row[3:].values[:-2]  # Shift the data in columns 3 and onward by 2 positions
    return row

# Loop over each PDF file
for pdf_path in pdf_files:
    # print("Processing:", pdf_path)

    # Open the PDF file using pdfplumber
    with pdfplumber.open(pdf_path) as pdf:
        start_pages = []
        dfs = []

        # Iterate over each page in the PDF
        for i, page in enumerate(pdf.pages):
            page_text = page.extract_text()

            # Check if "1. Location Parameters" is present in the page text
            if "1. Location Parameters" in page_text:
                start_pages.append(i)

        if start_pages:
            # Add the last page of the PDF as an end point to the list of start pages
            # This helps handle the case where the last "1. Location Parameters" occurs at the end of the PDF
            start_pages.append(len(pdf.pages))

            # Iterate over each start page
            for j in range(len(start_pages) - 1):
                temp_dfs = []
                start_page = start_pages[j]
                end_page = start_pages[j + 1]

                # Read the PDF file again, starting from the identified start page and ending at the next "1. Location Parameters" page
                for page in pdf.pages[start_page:end_page]:
                    tables = page.extract_tables()
                    for table in tables:
                        # Generate unique column names for each table
                        columns = [f"Column_{i}" for i in range(len(table[0]))]
                        df = pd.DataFrame(table[0:], columns=columns)
                        temp_dfs.append(df)

                if temp_dfs:
                    # Concatenate all tables into a single DataFrame
                    combined_df = pd.concat(temp_dfs, ignore_index=True)

                    combined_df = combined_df.apply(shift_data, axis=1)

                    combined_df = combined_df.drop(combined_df.columns[[4, 5]], axis=1)

                    # Shift first three rows to column 2
                    # combined_df.loc[0:3, 'Column_1'] = combined_df['Column_0']

                    # Drop unnecessary columns.
                    # combined_df = combined_df.drop(columns=["Column_0", "Column_3"]) #, "Column_7", "Column_8"

                    # Drop empty rows
                    # combined_df = combined_df.dropna(how='all')

                    # Remove line breaks
                    combined_df = combined_df.replace('\n', ' ', regex=True)

                    # Generate a unique output filename using a counter
                    filename = os.path.splitext(os.path.basename(pdf_path))[0]  # Get the base filename of the PDF
                    counter = 1
                    while True:
                        output_csv = os.path.join(output_folder, f"{filename}_output_{counter}.csv")
                        if not os.path.exists(output_csv):
                            break
                        counter += 1

                    output_csv = os.path.join(output_folder, f"{filename}_output_{j + 1}.csv")
                    
                    # Save the combined DataFrame as a CSV file
                    combined_df.to_csv(output_csv, header=None, index=False)
                    # print(f"Tables saved in {output_csv}")
                else:
                    print("No tables found in the PDF.")
        else:
            print("Unable to find '1. Location Parameters' in the PDF.")


#### 2018 Data

In [2]:
import glob
import os
import pdfplumber
import pandas as pd

# Folder path containing the PDF files
folder_path = "/Users/sid/Downloads/MA_AS/"

# Output folder path for saving CSV files
output_folder = "/Users/sid/Documents/MA_17/AS/"

# Get a list of PDF files in the folder
pdf_files = glob.glob(folder_path + "*.pdf")

# Function to shift data by 2 columns if Column 3 is not empty. Some pdfs formatting causes page 3 data to be misinterpretted. 
def shift_data(row):
    if row.name >= 30 and pd.notnull(row[3]):  # Check if row index is >= 30 and Column 3 is not empty
        row[5:] = row[3:].values[:-2]  # Shift the data in columns 3 and onward by 2 positions
    return row

# Get total number of PDF files
total_pdfs = len(pdf_files)
processed_pdfs = 0

# Define the intervals at which to print progress notifications
progress_intervals = [20, 40, 60, 80, 100]
current_interval = 0


# Loop over each PDF file
for pdf_path in pdf_files:
    # print("Processing:", pdf_path)

    # Open the PDF file using pdfplumber
    with pdfplumber.open(pdf_path) as pdf:
        start_pages = []
        dfs = []

        # Iterate over each page in the PDF
        for i, page in enumerate(pdf.pages):
            page_text = page.extract_text()

            # Check if "1. Location Parameters" is present in the page text
            if "1. Location Parameters" in page_text:
                start_pages.append(i)

        if start_pages:
            # Add the last page of the PDF as an end point to the list of start pages
            # This helps handle the case where the last "1. Location Parameters" occurs at the end of the PDF
            start_pages.append(len(pdf.pages))

            # Iterate over each start page
            for j in range(len(start_pages) - 1):
                temp_dfs = []
                start_page = start_pages[j]
                end_page = start_pages[j + 1]

                # Read the PDF file again, starting from the identified start page and ending at the next "1. Location Parameters" page
                for page in pdf.pages[start_page:end_page]:
                    tables = page.extract_tables()
                    for table in tables:
                        # Generate unique column names for each table
                        columns = [f"Column_{i}" for i in range(len(table[0]))]
                        df = pd.DataFrame(table[0:], columns=columns)
                        temp_dfs.append(df)

                if temp_dfs:
                    # Concatenate all tables into a single DataFrame
                    combined_df = pd.concat(temp_dfs, ignore_index=True)

                    combined_df = combined_df.apply(shift_data, axis=1)

                    combined_df = combined_df.drop(combined_df.columns[[7, 8]], axis=1)

                    # Shift first three rows to column 2
                    # combined_df.loc[0:3, 'Column_1'] = combined_df['Column_0']

                    # Drop unnecessary columns.
                    # combined_df = combined_df.drop(columns=["Column_0", "Column_3"]) #, "Column_7", "Column_8"

                    # Drop empty rows
                    # combined_df = combined_df.dropna(how='all')

                    # Remove line breaks
                    combined_df = combined_df.replace('\n', ' ', regex=True)

                    # Generate a unique output filename using a counter
                    filename = os.path.splitext(os.path.basename(pdf_path))[0]  # Get the base filename of the PDF
                    counter = 1
                    while True:
                        output_csv = os.path.join(output_folder, f"{filename}_output_{counter}.csv")
                        if not os.path.exists(output_csv):
                            break
                        counter += 1

                    output_csv = os.path.join(output_folder, f"{filename}_output_{j + 1}.csv")
                    
                    # Save the combined DataFrame as a CSV file
                    combined_df.to_csv(output_csv, header=None, index=False)
                    # print(f"Tables saved in {output_csv}")
                    #     # Increment the processed PDFs counter
                    # processed_pdfs += 1
                    
                    # # Calculate the progress percentage
                    # progress_percentage = (processed_pdfs / total_pdfs) * 100
                    
                    # # Check if the current progress is greater than or equal to the next interval
                    # if progress_percentage >= progress_intervals[current_interval]:
                    #     # Print progress notification
                    #     print(f"{progress_percentage:.2f}% of PDFs converted to CSVs")
                    #     # Move to the next interval
                    #     current_interval += 1
                        
                    # # Check if all intervals have been reached
                    # if current_interval >= len(progress_intervals):
                    #     break
                else:
                    print("No tables found in the PDF.")
        else:
            print("Unable to find '1. Location Parameters' in the PDF.")



### CSV Manipulation

#### Completed correct code below:
Works for 2020

In [ ]:
import pandas as pd
import os
import glob

## Change folder path and output_csv for each run
# Path to the folder containing the files
folder_path = "/Users/sid/Documents/MA_20/AN/"

# Get a list of files in the folder
file_list = glob.glob(os.path.join(folder_path, "*.csv"))

# Initialize an empty DataFrame to store the combined results
final_df = pd.DataFrame()

# Initialize a dictionary to store the shape counts
shape_counts = {}

# Loop over each file
for file_path in file_list:
    # Read the file into a DataFrame
    df2 = pd.read_csv(file_path)

    ## State info
    df4 = df2.drop(df2.index[3:], inplace=False) # only keep required rows
    df4 = df4.iloc[:, [0, 1]] # drops unnecesary columns
    df4 = df4.transpose().reset_index()
    df4.columns = df4.iloc[0]
    df4 = df4[1:]  # Remove the header row
    df4 = df4.reset_index(drop=True)

    ## District info
    df5 = df2.drop(df2.index[2:], inplace=False)
    df5 = df5.iloc[:, [2, 3]] ## changed index, different from TS
    df5 = df5.transpose().reset_index()
    df5.columns = df5.iloc[0]
    df5 = df5[1:]  # Remove the header row
    df5 = df5.reset_index(drop=True)

    ## Village Parameters
    df3 = df2.drop(df2.columns[0], axis=1) ## Added this, different from TS code
    df3 = df3.iloc[8:].transpose() ## if TS, df3 = df2.iloc
    df3 = df3.dropna(axis=1, how='all')  ## Added this, different from TS code
    # Extract the header row and set it as the column names
    df3.columns = df3.iloc[0]
    df3 = df3[1:]  # Remove the header row
    df3 = df3.iloc[1:]

    df3 = df3.reset_index(drop=True)

    # # # Remove row 1,3
    # rows_to_drop = [0,2] 
    # df3 = df3.drop(rows_to_drop)
    # df3 = df3.fillna(0)

    # Reset the index
    # df3 = df3.reset_index(drop=True)
    # df3 = df3.dropna(how='all')
    combined_df = pd.concat([df4, df5,df3], axis=1)
    # print(combined_df.shape[1])

    # Get the shape of combined_df
    df_shape = combined_df.shape

    # Increment the count for the shape in the dictionary
    if df_shape in shape_counts:
        shape_counts[df_shape] += 1
    else:
        shape_counts[df_shape] = 1

    # if combined_df.shape[1] == 54: ## Only use in 2018 data
    final_df = final_df.append(combined_df, ignore_index=True)
     
output_csv = "/Users/sid/Documents/MA_20/AN.csv"
final_df.to_csv(output_csv, index=False)
print(f"Combined results saved in {output_csv}")

# Print the shape counts
print("Shape Counts:")
for shape, count in shape_counts.items():
    print(f"Shape: {shape}, Count: {count}")
    

#### 2018 Trial

In [48]:
folder_path = "/Users/sid/Documents/MA_18/AN/00234465_f_20181227171958_output_1.csv"
df2 = pd.read_csv(folder_path)
df4 = df2.drop(df2.index[3:], inplace=False) # only keep required rows
df4 = df4.iloc[:, [0, 2]] # drops unnecesary columns
df4 = df4.transpose().reset_index()
df4.columns = df4.iloc[0]
df4 = df4[1:]  # Remove the header row
df4 = df4.reset_index(drop=True)
## District info
df5 = df2.drop(df2.index[2:], inplace=False)
df5 = df5.iloc[:, [4, 6]] ## changed index, different from TS
df5 = df5.transpose().reset_index()
df5.columns = df5.iloc[0]
df5 = df5[1:]  # Remove the header row
df5 = df5.reset_index(drop=True)

## Village Parameters
df3 = df2.drop(df2.columns[0], axis=1) ## Added this, different from TS code
df3 = df3.iloc[8:].transpose() ## if TS, df3 = df2.iloc
df3 = df3.dropna(axis=1, how='all')  ## Added this, different from TS code
# Extract the header row and set it as the column names
df3.columns = df3.iloc[0]
df3 = df3[4:5]  # Remove the header row
# df3 = df3.iloc[1:]

df3 = df3.reset_index(drop=True)

In [49]:
df3

Empty DataFrame
Columns: [Total Household, Total number of SHGs promoted, Total Area (in hectares), Net sown Area(In hectares), Total Un irrigated land area (in hectare), Area irrigated (in hectare), % households engaged exclusively in Farm  activitie, % households engaged exclusively in   Non-farm activities, Availability of banks, Availability of bank/Business correspondent  with internet connectivity, Availability of ATM, Whether the village is connected to All  weather road, Whether village has an internal cc/ brick  road, Availability of Public Transport, Availability of Internet Café/Common  Service Center, Availability of electricity for domestic  use(in Hrs), Availability of Public Distribution System  (PDS), Availability of markets, Availability of Piped tap water, Availability of Telephone Services, Total no of household using clean  energy (LPG/Bio gas), No of household with kuccha wall and  kuccha roof, Availability of Post office/Sub-Post office, Availability of School, Availability of Vocational Educational  Centre/ITI/RSETI/DDU-GKY, Availability of Sub centre /PHC/CHC, Availability of Veterinary Clinic Hospital, Availability of drainage facilities, Availability of Soil Testing Centres, Availability of government Seed, Availability of Fertilizer Shop, Community waste disposal system, Community bio gas or recycle of waste  for production use, Is the village Open Defacation Free, Availability Of Aanganwadi Centre, No of total children in the age group of 0-3  years, No of children aged 0-3 years registered  under Aanganwadi, No of children aged 0-3 years immunized, No of children categorized as Non- Stunted as per ICDS record, No. of households mobilized into SHGs, No. of households mobilized into  Producer Groups (PGs), No. of households supported by village  based Agricultural Extension Workers, No. of households supported by village  based Livestock Extension Workers, No. of SHGs accessed bank loans]
Index: []

[0 rows x 44 columns]

In [3]:
df2

State:  \
0                            Sub District :   
1                          Gram Panchayat :   
2                                     PIN :   
3                       2. Basic Parameters   
4                                      S.NO   
5                                         1   
6                                         2   
7                                         3   
8                                         4   
9                                         5   
10                                        6   
11                                        7   
12                                        8   
13                                        9   
14         3. Key Infrastructure Parameters   
15                                       10   
16                                       11   
17                                       12   
18                                       13   
19                                       14   
20                                       15   
21                                       16   
22                                       17   
23                                       18   
24                                       19   
25                                       20   
26                                       21   
27                                       22   
28                                       23   
29                                       24   
30                                       25   
31                                       26   
32                                       27   
33                                       28   
34                                       29   
35                                       30   
36                                       31   
37  4. Economic development and livelihoods   
38                                       32   
39                                       33   
40                                       34   
41      5. Health, nutrition and sanitation   
42                                       35   
43                                       36   
44                                       37   
45                                       38   
46                                       39   
47                                       40   
48                                       41   
49                                       42   
50                     6. Women Empowerment   
51                                       43   
52                                       44   
53                                       45   
54                                       46   
55                   7. Financial Inclusion   
56                                       47   

                                           Unnamed: 1  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                            Question   
5                                    Total Population   
6                                                Male   
7                                              Female   
8                                     Total Household   
9                       Total number of SHGs promoted   
10                           Total Area (in hectares)   
11                         Net sown Area(In hectares)   
12          Total Un irrigated land area (in hectare)   
13                        Area irrigated (in hectare)   
14                                                NaN   
15  % households engaged exclusively in Farm  acti...   
16  % households engaged exclusively in   Non-farm...   
17                              Availability of banks   
18  Availability of bank/Business correspondent  w...   
19                                Availability of ATM   
20  Whether the village is connected to All  weath...   
21    Whether village has an internal cc/ brick  road   

In [59]:
import pandas as pd
import os
import glob

## Change folder path and output_csv for each run
# Path to the folder containing the files
folder_path = "/Users/sid/Documents/MA_18/MH/folder5/"

# Get a list of files in the folder
file_list = glob.glob(os.path.join(folder_path, "*.csv"))

# Initialize an empty DataFrame to store the combined results
final_df = pd.DataFrame()

# Initialize a dictionary to store the shape counts
shape_counts = {}

# Loop over each file
for file_path in file_list:
    # Read the file into a DataFrame
    df2 = pd.read_csv(file_path)

    ## State info
    df4 = df2.drop(df2.index[3:], inplace=False) # only keep required rows
    df4 = df4.iloc[:, [0, 2]] # drops unnecesary columns, different compared to 2020
    df4 = df4.transpose().reset_index()
    df4.columns = df4.iloc[0]
    df4 = df4[1:]  # Remove the header row
    df4 = df4.reset_index(drop=True)

    ## District info
    df5 = df2.drop(df2.index[2:], inplace=False)
    df5 = df5.iloc[:, [4, 6]] ## changed index, different from TS, different compared to 2020
    df5 = df5.transpose().reset_index()
    df5.columns = df5.iloc[0]
    df5 = df5[1:]  # Remove the header row
    df5 = df5.reset_index(drop=True)

    ## Village Parameters
    df3 = df2.drop(df2.columns[0], axis=1) ## Added this, different from TS code
    df3 = df3.iloc[5:].transpose() ## if TS, df3 = df2.iloc
    df3 = df3.dropna(axis=1, how='all')  ## Added this, different from TS code
    # Extract the header row and set it as the column names
    df3.columns = df3.iloc[0]
    df3 = df3[4:5]  # Remove the header row, only keep 2018 data row
    # df3 = df3.iloc[1:]

    df3 = df3.reset_index(drop=True)

    # # # Remove row 1,3
    # rows_to_drop = [0,2] 
    # df3 = df3.drop(rows_to_drop)
    # df3 = df3.fillna(0)

    # Reset the index
    # df3 = df3.reset_index(drop=True)
    # df3 = df3.dropna(how='all')
    combined_df = pd.concat([df4, df5,df3], axis=1)
    # print(combined_df.shape[1])

    # Get the shape of combined_df
    df_shape = combined_df.shape

    # Increment the count for the shape in the dictionary
    if df_shape in shape_counts:
        shape_counts[df_shape] += 1
    else:
        shape_counts[df_shape] = 1

    # if combined_df.shape[1] == 54: ## Only use in 2018 data
    final_df = final_df.append(combined_df, ignore_index=True)
     
output_csv = "/Users/sid/Documents/MA_18/MH5.csv"
final_df.to_csv(output_csv, index=False)
print(f"Combined results saved in {output_csv}")

# Print the shape counts
# print("Shape Counts:")
for shape, count in shape_counts.items():
    print(f"Shape: {shape}, Count: {count}")
    

/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

Combined results saved in /Users/sid/Documents/MA_18/MH5.csv
Shape: (1, 54), Count: 3765


/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_55381/2177026432.py:71: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

#### Master Folder loop code below:

In [5]:
import pandas as pd
import os
import glob
import time

# Path to the master folder containing subfolders
master_folder = "/Users/sid/Documents/MA_17/AS/"

# Get a list of subfolders in the master folder
subfolders = [subfolder for subfolder in os.listdir(master_folder) if os.path.isdir(os.path.join(master_folder, subfolder))]

# Loop through each subfolder
for subfolder in subfolders:
    # if subfolder != "UP":
    #     print(f"Skipping folder {subfolder}.\n")
    #     continue  # Skip processing this folder and move to the next

    folder_path = os.path.join(master_folder, subfolder)
    
    # Get a list of files in the subfolder
    file_list = glob.glob(os.path.join(folder_path, "*.csv"))

    print(f"Beginning folder {subfolder}.\n")

    start_time = time.time()

    final_df = pd.DataFrame()
    shape_counts = {}
    
    for file_path in file_list:
        df2 = pd.read_csv(file_path)

        ## State info
        df4 = df2.drop(df2.index[3:], inplace=False) # only keep required rows
        df4 = df4.iloc[:, [0, 2]] # drops unnecesary columns
        df4 = df4.transpose().reset_index()
        df4.columns = df4.iloc[0]
        df4 = df4[1:]  # Remove the header row
        df4 = df4.reset_index(drop=True)

        ## District info
        df5 = df2.drop(df2.index[2:], inplace=False)
        df5 = df5.iloc[:, [4, 6]] ## changed index, different from TS
        df5 = df5.transpose().reset_index()
        df5.columns = df5.iloc[0]
        df5 = df5[1:]  # Remove the header row
        df5 = df5.reset_index(drop=True)

        ## Village Parameters
        # df3 = df2.drop(df2.columns[0], axis=1) ## Added this, different from TS code
        # df3 = df3.iloc[8:].transpose() ## if TS, df3 = df2.iloc
        # df3 = df3.dropna(axis=1, how='all')  ## Added this, different from TS code
        # # Extract the header row and set it as the column names
        # df3.columns = df3.iloc[0]
        # df3 = df3[1:]  # Remove the header row
        # df3 = df3.iloc[1:]

        # df3 = df3.reset_index(drop=True)

        df3 = df2.drop(df2.columns[0], axis=1) ## Added this, different from TS code
        df3 = df3.iloc[5:].transpose() ## if TS, df3 = df2.iloc
        df3 = df3.dropna(axis=1, how='all')  ## Added this, different from TS code
        # Extract the header row and set it as the column names
        df3.columns = df3.iloc[0]
        df3 = df3[4:5]  # Remove the header row, only keep 2018 data row

        df3 = df3.reset_index(drop=True)

        combined_df = pd.concat([df4, df5,df3], axis=1)

        # Get the shape of combined_df
        df_shape = combined_df.shape

        # Increment the count for the shape in the dictionary
        if df_shape in shape_counts:
            shape_counts[df_shape] += 1
        else:
            shape_counts[df_shape] = 1

        # if combined_df.shape[1] == 54: ## Only use in 2018 data
        final_df = final_df.append(combined_df, ignore_index=True)

    # Calculate time taken
    end_time = time.time()
    time_taken = end_time - start_time
    
    # Save combined results to CSV
    output_csv = os.path.join(master_folder, f"{subfolder}.csv")
    final_df.to_csv(output_csv, index=False)
    print(f"Combined results for {subfolder} saved in {output_csv}")

    # Print shape counts
    print("Shape Counts:")
    for shape, count in shape_counts.items():
        print(f"Shape: {shape}, Count: {count}")

    print(f"Folder {subfolder} completed in {time_taken:.2f} seconds.\n")


Beginning folder folder2.



/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

Combined results for folder2 saved in /Users/sid/Documents/MA_17/AS/folder2.csv
Shape Counts:
Shape: (1, 54), Count: 10000
Folder folder2 completed in 68.72 seconds.

Beginning folder folder3.



/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

Combined results for folder3 saved in /Users/sid/Documents/MA_17/AS/folder3.csv
Shape Counts:
Shape: (1, 54), Count: 6382
Folder folder3 completed in 39.08 seconds.

Beginning folder folder1.



/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

Combined results for folder1 saved in /Users/sid/Documents/MA_17/AS/folder1.csv
Shape Counts:
Shape: (1, 54), Count: 10000
Folder folder1 completed in 43.69 seconds.



/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(combined_df, ignore_index=True)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3144142590.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas i

In [ ]:
import pandas as pd
import os

# Specify the directory containing CSV files
csv_directory = "/Users/sid/Documents/MA_20/"

# Get a list of all CSV files in the directory
csv_files = [file for file in os.listdir(csv_directory) if file.endswith(".csv")]

# Dictionary to store column sets
column_sets = {}

# Loop through each CSV file
for csv_file in csv_files:
    file_path = os.path.join(csv_directory, csv_file)
    
    # Read the CSV file using pandas
    df = pd.read_csv(file_path)
    
    # Get the shape of the DataFrame
    shape = df.shape
    
    # Get the set of columns
    columns = tuple(df.columns)
    
    # Store the columns and shape in the dictionary
    column_sets[file_path] = (shape, columns)

# Create a dictionary to group files with same columns
column_groups = {}

# Group files with same columns
for file, (shape, columns) in column_sets.items():
    columns_key = tuple(columns)
    
    if columns_key in column_groups:
        column_groups[columns_key].append((file, shape))
    else:
        column_groups[columns_key] = [(file, shape)]

# Print grouped information
for columns_key, files_and_shapes in column_groups.items():
    if len(files_and_shapes) > 1:
        file_info = [f"{os.path.basename(file)} ({shape})" for file, shape in files_and_shapes]
        print(f"Files {', '.join(file_info)} have the same columns.")
    else:
        file_info = files_and_shapes[0]
        print(f"File {os.path.basename(file_info[0])} ({file_info[1]}) has different columns.")

print("Comparison finished.")


In [ ]:
import pandas as pd
import os

# Specify the directory containing CSV files
csv_directory = "/Users/sid/Documents/MA_20/"

# Get a list of all CSV files in the directory
csv_files = [file for file in os.listdir(csv_directory) if file.endswith(".csv")]

# Dictionary to store column sets
column_sets = {}

# Loop through each CSV file
for csv_file in csv_files:
    file_path = os.path.join(csv_directory, csv_file)
    
    # Read the CSV file using pandas
    df = pd.read_csv(file_path)
    
    # Get the shape of the DataFrame
    shape = df.shape
    
    # Get the set of columns
    columns = tuple(df.columns)
    
    # Store the columns and shape in the dictionary
    column_sets[file_path] = (shape, columns)

# Create a dictionary to group files with same columns
column_groups = {}

# Group files with same columns
for file, (shape, columns) in column_sets.items():
    columns_key = tuple(columns)
    
    if columns_key in column_groups:
        column_groups[columns_key].append((file, shape))
    else:
        column_groups[columns_key] = [(file, shape)]

# Concatenate files with similar columns
output_counter = 1
for columns_key, files_and_shapes in column_groups.items():
    if len(files_and_shapes) > 1:
        # Extract paths of files with same columns
        file_paths = [file for file, shape in files_and_shapes]
        
        # Read and concatenate the dataframes
        dfs = [pd.read_csv(file_path) for file_path in file_paths]
        combined_df = pd.concat(dfs, ignore_index=True)
        
        # Create an output file name using incremental numbering
        output_file = os.path.join(csv_directory, f"{output_counter}.csv")
        
        # Save the combined dataframe to the output file name
        combined_df.to_csv(output_file, index=False)
        print(f"Combined files with {columns_key} columns saved as {output_file}")
        
        output_counter += 1

print("Comparison and concatenation finished.")


### CSV Final

In [8]:
import os
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


def process_csv(file_path, output_folder):
    # Load the CSV file into a DataFrame
    df = pd.read_csv(file_path)

    # Step 1: Remove ':' from each column name
    df.columns = [col.replace(':', '').strip() for col in df.columns]

    # Define the columns and the corresponding lengths for the codes
    columns_and_lengths = {
        'State': 4,
        'Sub District': 6,
        'Gram Panchayat': 8,
        'District': 5,
        'Development Block': 6,
        'Village': 9
    }

    # Step 2: Add new columns for the codes and modify the original columns
    for col, length in columns_and_lengths.items():
        if col in df.columns:
            code_col = col + ' code'
            df[code_col] = df[col].apply(lambda x: x[-length:] if isinstance(x, str) else x)
            df[code_col] = df[code_col].str.replace('(', '').str.replace(')', '')  # Remove parentheses
            df[col] = df[col].apply(lambda x: x[:-length] if isinstance(x, str) else x)

    # Step 3: Reorder columns to place code columns next to their originals
    new_order = []
    for col in df.columns:
        if col in columns_and_lengths:
            new_order.append(col)
            new_order.append(col + ' code')
        elif ' code' not in col:
            new_order.append(col)

    # Make sure to add any remaining columns that weren't part of the intended columns
    for col in df.columns:
        if col not in new_order:
            new_order.append(col)

    df = df[new_order]

    # Save the modified DataFrame to a new CSV file
    output_file_path = os.path.join(output_folder, os.path.basename(file_path))
    df.to_csv(output_file_path, index=False)

def process_folder(input_folder, output_folder):
    # Create the output folder if it doesn't exist
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Process each CSV file in the input folder
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            process_csv(file_path, output_folder)

# Define input and output folders
input_folder = '/Users/sid/Documents/MA_17/_final csvs'
output_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'

# Process all CSV files in the input folder and save the modified files to the output folder
process_folder(input_folder, output_folder)

print("Processing complete.")


/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3790834740.py:9: DtypeWarning: Columns (54,55,56,57,58,59) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3790834740.py:9: DtypeWarning: Columns (55,56,58) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3790834740.py:9: DtypeWarning: Columns (55,56,57,58,59) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3790834740.py:9: DtypeWarning: Columns (55,59) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
/var/folders/gk/2dbxfg1d3g96xh9f5t1plpg00000gn/T/ipykernel_11232/3790834740.py:9: DtypeWarning: Columns (57) hav

Processing complete.


In [15]:
import os
import pandas as pd
import warnings

def print_csv_dimensions_and_mixed_types(input_folder):
    # Suppress DtypeWarning
    warnings.filterwarnings('ignore', category=pd.errors.DtypeWarning)
    
    # Process each CSV file in the input folder
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            # Load the CSV file into a DataFrame
            df = pd.read_csv(file_path)
            # Print the dimensions of the DataFrame
            print(f"File: {file_name} - Rows: {df.shape[0]}, Columns: {df.shape[1]}")
            # Identify columns with mixed types
            mixed_type_columns = []
            for col in df.columns:
                unique_types = df[col].map(type).unique()
                if len(unique_types) > 1:
                    mixed_type_columns.append(col)
            # Print the columns with mixed types
            if mixed_type_columns:
                print(f"File: {file_name} - Columns with mixed types: {mixed_type_columns}")

# Define input folder
input_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'

# Print dimensions and mixed type columns of all CSV files in the input folder
print_csv_dimensions_and_mixed_types(input_folder)

print("Processing complete.")


File: OR.csv - Rows: 27946, Columns: 66
File: OR.csv - Columns with mixed types: ['Availability of banks', 'Availability of bank/Business correspondent  with internet connectivity', 'Availability of ATM', 'Whether the village is connected to All  weather road', 'Whether village has an internal cc/ brick  road', 'Availability of Public Transport', 'Availability of Internet Café/Common  Service Center', 'Availability of electricity for domestic  use(in Hrs)', 'Availability of Public Distribution System  (PDS)', 'Availability of markets', 'Availability of Piped tap water', 'Availability of Telephone Services', 'Availability of Post office/Sub-Post office', 'Availability of School', 'Availability of Vocational Educational  Centre/ITI/RSETI/DDU-GKY', 'Availability of Sub centre /PHC/CHC', 'Availability of Veterinary Clinic Hospital', 'Availability of drainage facilities', 'Availability of Soil Testing Centres', 'Availability of government Seed', 'Availability of Fertilizer Shop', 'Community

In [14]:
import os
import pandas as pd
import warnings

def get_reference_columns(input_folder):
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            df = pd.read_csv(file_path)
            if df.shape[1] == 66:
                return df.columns.tolist()
    raise ValueError("No CSV file with exactly 66 columns found in the folder.")

def align_columns(df, reference_columns):
    # Add missing columns with NaN values
    for col in reference_columns:
        if col not in df.columns:
            df[col] = pd.NA
    # Drop extra columns
    df = df[reference_columns]
    return df

def process_csv(file_path, reference_columns, output_folder):
    # Load the CSV file into a DataFrame
    df = pd.read_csv(file_path)
    
    # Align columns
    df_aligned = align_columns(df, reference_columns)
    
    # Save the modified DataFrame to a new CSV file
    output_file_path = os.path.join(output_folder, os.path.basename(file_path))
    df_aligned.to_csv(output_file_path, index=False)

def process_folder(input_folder, output_folder):
    # Create the output folder if it doesn't exist
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Get the reference columns from a CSV file with exactly 66 columns
    reference_columns = get_reference_columns(input_folder)
    
    # Process each CSV file in the input folder
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            process_csv(file_path, reference_columns, output_folder)

# Define input and output folders
input_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'
output_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'

# Process all CSV files in the input folder and save the modified files to the output folder
process_folder(input_folder, output_folder)

print("Processing complete.")


Processing complete.


In [16]:
import os
import pandas as pd
import warnings

def get_reference_columns(input_folder):
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            df = pd.read_csv(file_path)
            if df.shape[1] == 66:
                return df.columns.tolist()
    raise ValueError("No CSV file with exactly 66 columns found in the folder.")

def align_columns(df, reference_columns):
    # Add missing columns with NaN values
    for col in reference_columns:
        if col not in df.columns:
            df[col] = pd.NA
    # Drop extra columns
    df = df[reference_columns]
    return df

def process_csv(file_path, reference_columns, output_folder):
    # Load the CSV file into a DataFrame
    df = pd.read_csv(file_path)
    
    # Align columns
    df_aligned = align_columns(df, reference_columns)
    
    # Save the modified DataFrame to a new CSV file
    output_file_path = os.path.join(output_folder, os.path.basename(file_path))
    df_aligned.to_csv(output_file_path, index=False)
    
    return df_aligned

def process_folder(input_folder, output_folder):
    # Create the output folder if it doesn't exist
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Get the reference columns from a CSV file with exactly 66 columns
    reference_columns = get_reference_columns(input_folder)
    
    # Initialize an empty list to hold all DataFrames
    all_dfs = []
    
    # Process each CSV file in the input folder
    for file_name in os.listdir(input_folder):
        if file_name.endswith('.csv'):
            file_path = os.path.join(input_folder, file_name)
            df_aligned = process_csv(file_path, reference_columns, output_folder)
            all_dfs.append(df_aligned)
    
    # Concatenate all DataFrames into one
    final_df = pd.concat(all_dfs, ignore_index=True)
    
    # Save the final concatenated DataFrame to a new CSV file
    final_output_path = os.path.join(output_folder, '/Users/sid/Documents/MA_17/final_concatenated.csv')
    final_df.to_csv(final_output_path, index=False)
    
    print(f"Final concatenated file saved to: {final_output_path}")

# Define input and output folders
input_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'
output_folder = '/Users/sid/Documents/MA_17/_final csvs/_cleaned'

# Process all CSV files in the input folder and save the modified files to the output folder
process_folder(input_folder, output_folder)

print("Processing complete.")


Final concatenated file saved to: /Users/sid/Documents/MA_17/final_concatenated.csv
Processing complete.
